In [118]:
import pickle

'''
#Biology dataset for question body + title
cs_ques_dict = pickle.load(open("../clustering/bio_ques_dict.dat","rb"))
cs_cluster_centers = pickle.load(open("../clustering/bio_cluster_centers.dat","rb"))
#cs_cluster_centers_indices = pickle.load(open("../clustering/bio_cluster_centers_indices.dat","rb"))
'''

'''
#Biology dataset for question body + title +tag
ques_dict = pickle.load(open("../clustering/bio_withtags_ques_dict.dat","rb"))
cluster_centers = pickle.load(open("../clustering/bio_withtags_cluster_centers.dat","rb"))
#cs_cluster_centers_indices = pickle.load(open("../clustering/bio_cluster_centers_indices.dat","rb"))
'''

'''
#Biology dataset for question title only
ques_dict = pickle.load(open("../clustering/bio_onlytitle_ques_dict.dat","rb"))
cluster_centers = pickle.load(open("../clustering/bio_onlytitle_cluster_centers.dat","rb"))
#cluster_centers_indices = pickle.load(open("../clustering/bio_onlytitle_cluster_centers_indices.dat","rb"))
'''

#DataScience dataset for question title+tag+body
ques_dict = pickle.load(open("../clustering/n_ds_withtags_ques_dict.dat","rb"))
cluster_centers = pickle.load(open("../clustering/n_ds_withtags_cluster_centers.dat","rb"))


ans_dict = pickle.load(open("../clustering/n_ds_ans_dict.dat","rb"))
ans_cluster_centers = pickle.load(open("../clustering/n_ds_ans_cluster_centers.dat","rb"))
#ans_cluster_centers_indices = pickle.load(open("../clustering/biology_ans_cluster_centers_indices.dat","rb"))

In [119]:
num_clusters = cluster_centers.shape[0]
print("Total number of clusters: ",num_clusters)

Total number of clusters:  633


In [67]:
ans_num_clusters = ans_cluster_centers.shape[0]
print("Total number of answer clusters: ",ans_num_clusters)

Total number of answer clusters:  785


In [120]:
#We have the cluster centers and also the label for each question
#For a given cluster, find its 10 nearby clusters, sorted according to their distances
#nearest first
#Use euclidean distance between the cluster centers for this
from sklearn.metrics.pairwise import euclidean_distances

def computeNearByClusters(cluster_centers):
    nearby_centers_dict = {}
    for i in range(len(cluster_centers)):
        #gives the distance of i-th center from all the centers
        distances = euclidean_distances(cluster_centers,[cluster_centers[i]])
        #sort these distances
        nearest_10_centers_array = distances.argsort(axis=0)[0:6]
        nearest_10_centers = []
        for elem in nearest_10_centers_array:
            nearest_10_centers.append(elem[0])
        if not i in nearby_centers_dict:
            nearby_centers_dict[i] = nearest_10_centers
    return nearby_centers_dict

In [121]:
#Dict where key = cluster_id, value = list of ids of 10 nearest clusters
nearby_centers_dict = computeNearByClusters(cluster_centers)

In [68]:
ans_nearby_centers_dict = computeNearByClusters(ans_cluster_centers)

In [48]:
print(nearby_centers_dict[0])

[0, 110, 986, 359, 888, 7]


In [122]:
#Given a cluster, find all the questions/answers that belong to it
def findAllInCluster(num_clusters,dictionary):
    cluster_dict = {}
    for key, value in dictionary.items():
        if value[1] in cluster_dict:
            cluster_dict[value[1]].append(key)
        else:
            cluster_dict[value[1]] = [key]
    return cluster_dict
    

In [123]:
#dict where key = cluster_id
#value = list of all questions present in that cluster
questions_in_a_cluster_dict= {}
questions_in_a_cluster_dict = findAllInCluster(num_clusters,ques_dict)

In [69]:
answers_in_a_cluster_dict={}
answers_in_a_cluster_dict = findAllInCluster(ans_num_clusters,ans_dict)

In [12]:
print(questions_in_a_cluster_dict[0])
print(answers_in_a_cluster_dict[0])

[211, 280, 671, 1061, 2448, 3718, 5249, 5502, 6681, 8227, 9207, 9224, 9924, 9978, 10063, 10200, 11096, 11237, 12059, 12633, 14125, 15085, 15257, 16783, 18368, 18595, 19051, 19442, 20095, 20165, 22026, 22981, 23196, 23504, 23862, 23966, 24010, 24929, 25005, 25921, 25933, 27311, 27436, 27552, 28239, 28552, 28716, 29062, 29437, 31426, 31787, 32627, 32799, 33126, 33151, 36006, 36206, 36897, 38363, 38410, 39636, 39915, 40564, 41759, 42771, 43170, 43827, 44680, 44888, 45511, 45883, 46007]
[28]


In [124]:
#to remove the XML content from the tags
import re
def processTags(temp):
    temp = re.sub(r"<"," ",temp)
    temp = re.sub(r">"," ",temp)
    temp = temp.strip()
    temp = temp.replace("  "," ")
    return temp

In [125]:
#TF-IDF part
import pandas as pd

df_ques = pd.read_csv("../csv_files/DS_questions.csv")
df_ques['Tags'] = df_ques['Tags'].apply(lambda x:processTags(x))
df_question_merged = df_ques.Body.astype(str) + " " + df_ques.Title.astype(str)+ " "+ df_ques.Tags.astype(str)
df_ans = pd.read_csv("../csv_files/DS_answers.csv")

In [126]:
from sklearn.feature_extraction.text import TfidfVectorizer
tf = TfidfVectorizer(analyzer='word',ngram_range=(1, 2),min_df=0, stop_words='english')
tfidf_matrix_ques = tf.fit_transform(df_question_merged)
tfidf_matrix_ans = tf.fit_transform(df_ans['Body'])

In [127]:
print("Shape of tf-idf question matrix is: ",tfidf_matrix_ques.shape)
print("Shape of tf-idf answer matrix is: ",tfidf_matrix_ans.shape)

Shape of tf-idf question matrix is:  (14481, 819503)
Shape of tf-idf answer matrix is:  (16785, 758920)


In [128]:
#We also need a list which gives the reverse lookup from id to index of the list
idx_ques_list = []
for index, row in df_ques.iterrows():
    idx = row['Id']
    idx_ques_list.append(idx)

In [73]:
#We also need a list which gives the reverse lookup from id to index of the list
idx_ans_list = []
for index, row in df_ans.iterrows():
    idx = row['Id']
    idx_ans_list.append(idx)

In [129]:
#Given a question, find which cluster it belongs to
#find all nearby clusters to that cluster
#retrieve all the questions from the nearby clusters, form a list of all the questions
#Do cosine similarity to find the questions most similar to the given question
#return top 10 of them

from sklearn.metrics.pairwise import cosine_similarity
import numpy as np

def generateQuesRecommendations(ques_id):
    total_questions = []
    #input is question_id
    #cluster_label tells which cluster the question is in
    #ques_dict is a dictionary where key is ques_id and value is a tuple(embedding,label)
    cluster_label = ques_dict[ques_id][1]
    #find the 10 nearby clusters to a given cluster
    nearby_clusters = nearby_centers_dict[cluster_label]
    #nearby_clusters is a list
    for cluster in nearby_clusters:
        total_questions.extend(questions_in_a_cluster_dict[cluster])
    input_tf = tfidf_matrix_ques[idx_ques_list.index(ques_id)]
    #total_questions is a list of all questions
    #for a given question find cosine similarity with all these questions
    cosine_scores = []
    temp = cosine_similarity(ques_dict[ques_id][0].reshape(1,-1), [ques_dict[ques][0] for ques in total_questions])
    idx_list = [idx_ques_list.index(ques) for ques in total_questions]
    temp_tfidf = cosine_similarity(input_tf, tfidf_matrix_ques[idx_list])
    #taking the average of both embeddings and TF-IDF methods
    temp_avg = (temp + temp_tfidf)/2
    cosine_scores = [(total_questions[i], temp_avg[:,i][0]) for i in range(len(total_questions))]
    cosine_scores.sort(key=lambda x: x[1],reverse=True)
    return cosine_scores[0:100]

In [74]:
import pandas as pd

answersDF = pd.read_csv('../csv_files/DS_answers.csv')

answers ={}

#Building a dictionary of answerId with associated questionId
for index, row in answersDF.iterrows():
    answers[row['Id']] = row['ParentId']
    
#lookup parentID(Question ID) for answers
def lookupParentId(ansId):
    return answers[ansId]


In [75]:
def generateAnswerRecommendations(ans_id):
    total_answers = []
    #input is ans_id
    #cluster_label tells which cluster the question is in
    #ans_dict is a dictionary where key is ans_id and value is a tuple(embedding,label)
    cluster_label = ans_dict[ans_id][1]
    #find the 10 nearby clusters to a given cluster
    nearby_clusters = ans_nearby_centers_dict[cluster_label]
    #nearby_clusters is a list
    for cluster in nearby_clusters:
        total_answers.extend(answers_in_a_cluster_dict[cluster])
    input_tf = tfidf_matrix_ans[idx_ans_list.index(ans_id)]
    #total_questions is a list of all questions
    #for a given question find cosine similarity with all these answers
    #finally lookup the question id of the similar answer and store it with the cosine similarity between the answers
    cosine_scores = []
    cosine_embedding_scores = cosine_similarity(ans_dict[ans_id][0].reshape(1,-1), [ans_dict[ans][0] for ans in total_answers])
    idx_list = [idx_ans_list.index(ans) for ans in total_answers]
    cosine_tfidf_scores = cosine_similarity(input_tf, tfidf_matrix_ans[idx_list])
    temp_avg = (cosine_embedding_scores + cosine_tfidf_scores)/2
    cosine_scores = [(lookupParentId(total_answers[i]), temp_avg[:,i][0]) for i in range(len(total_answers))]
    cosine_scores.sort(key=lambda x: x[1],reverse=True)
    return cosine_scores[0:100]

In [130]:
#For a given question, generate top 10 recommendations
#output is a dict, which has ques_id as key, and value as list of tuples
#where each tuple consists of ques_id and cosine similarity score
ques_recommendations = {}
for key, value in ques_dict.items():
    #here key represents the question_id
    #generate recommendation for each such question
    ques_recommendations[key] = generateQuesRecommendations(key)


In [131]:
len(ques_recommendations)

14481

In [76]:
ans_recommendations = {}
for key, value in ans_dict.items():
    #here key represents the question_id based on answer embedding
    #generate recommendation for each such question
    #Based on answer similarities, find question recommendations
    que= lookupParentId(key)
    if que in ans_recommendations.keys():
        ans_recommendations[que].extend(generateAnswerRecommendations(key))
    else:
        ans_recommendations[que] = generateAnswerRecommendations(key)

In [60]:
len(ans_recommendations)

17279

In [132]:
ans_recommendations = pickle.load(open("n_ds_ans_hybrid_recommendations.dat","rb"))

In [73]:
def combine(ans_recommendations,ques_recommendations):
    ques_ans_recommendations = {}
    for key,val in ans_recommendations.items():
        if key in ques_ans_recommendations.keys():
            ques_ans_recommendations[key].extend(ans_recommendations[key])
        else:
            ques_ans_recommendations[key] = ans_recommendations[key]
    for key,val in ques_recommendations.items():
        if key in ques_ans_recommendations.keys():
            ques_ans_recommendations[key].extend(ques_recommendations[key])
        else:
            ques_ans_recommendations[key] = ques_recommendations[key]
    return ques_ans_recommendations
            
            

In [71]:
ques_recommendations = pickle.load(open("n_ds_ques_hybrid_recommendations.dat","rb"))
ans_recommendations = pickle.load(open("n_ds_ans_hybrid_recommendations.dat","rb"))

In [84]:
combinedRecommendations = combine(ans_recommendations,ques_recommendations)
len(combinedRecommendations)

14481

In [86]:
print(type(combinedRecommendations[5]))

<class 'list'>


In [82]:
def Sort_Tuple(tup):   
    return(sorted(tup, key = lambda x: x[1],reverse=True))

for key,value in combinedRecommendations.items():
    temp = []
    for tup in combinedRecommendations[key]:
        if(key==tup[0]):
            continue
        else:
            temp.append(tup)
    combinedRecommendations[key]=set(temp)
    t = Sort_Tuple(combinedRecommendations[key])
    combinedRecommendations[key] = t

[(11812, 0.5029358172489086), (36041, 0.5007550251288811), (10884, 0.49927309443708356), (16729, 0.4971054842918114), (40342, 0.49702073644005174), (40800, 0.49596966639197615), (28244, 0.4958804346227249), (1017, 0.4955359770558554), (31555, 0.49449201017673655), (8090, 0.49448239027770285), (20222, 0.493714789431288), (11399, 0.4934883725992169), (1253, 0.493386140213761), (29471, 0.49255733882403857), (38434, 0.49252941108712534), (37990, 0.4924557587916889), (33720, 0.4921525521406549), (27476, 0.4919845449998265), (26155, 0.49176751440576005), (39915, 0.4916104451277156), (13082, 0.49093596948405843), (38833, 0.4909264760604702), (27218, 0.4907835109633204), (22153, 0.4903507546170055), (36741, 0.4902405105586239), (6675, 0.49018389847455707), (41725, 0.48987067478038043), (22335, 0.4898590838526223), (31620, 0.48978872014197516), (5791, 0.4896717892732033), (27408, 0.4892912598058486), (29179, 0.48870700150188046), (11167, 0.4885987553124257), (46388, 0.4885003975805559), (41696,

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[(11247, 0.488536634976507), (32196, 0.48664734427909456), (30309, 0.48631689744730966), (16616, 0.4823225246504207), (14156, 0.4816070786636216), (10386, 0.48002054462913174), (10499, 0.47946834462273263), (32143, 0.47705552096927467), (28649, 0.47678654651080093), (9413, 0.4753809020320432), (11404, 0.4748064414583679), (12188, 0.47435122563796256), (30575, 0.47361844877369935), (6776, 0.4731412047120686), (26236, 0.4722051971893909), (31812, 0.4720666014849596), (979, 0.4719205743134342), (17991, 0.4719089100480836), (2255, 0.4717775080518446), (25004, 0.47175128709845043), (305, 0.47170269321640945), (1143, 0.4716257168631852), (2507, 0.47112083249039993), (15922, 0.47108002409222227), (424, 0.4710727886689814), (11970, 0.47102447756821847), (46259, 0.47052658226349386), (10585, 0.4701849169124513), (28504, 0.469877375338863), (43002, 0.46984020744134253), (8983, 0.46980547644522114), (33191, 0.4695864896390842), (6590, 0.46866403142413904), (16640, 0.46847030710836557), (21719, 0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[(37838, 0.5193185533025385), (11379, 0.5181852145866509), (8444, 0.5052624260319878), (22, 0.49965875077824223), (36851, 0.4988108899146814), (29879, 0.49752837123836413), (32846, 0.4974448890104953), (28293, 0.4973569318208814), (35781, 0.49653369185098056), (18013, 0.4946982767171814), (14964, 0.49246211065989276), (4967, 0.4921227803740817), (8369, 0.49199586738543616), (31113, 0.49175065166094284), (31798, 0.49162242393849065), (24452, 0.4912276167583511), (28114, 0.49114353209614114), (8294, 0.49105047951776015), (26550, 0.49097807726059906), (19380, 0.4908400152015126), (40957, 0.4908361004582645), (4914, 0.490518747759226), (38094, 0.49026420641004914), (35695, 0.4898654228924545), (37480, 0.48974522448225183), (29470, 0.4895717110432135), (29197, 0.4894975368757186), (10728, 0.4892415850805813), (32468, 0.48891579875041496), (31926, 0.4881079848450387), (31652, 0.4880809956407384), (42786, 0.48749294589306624), (13357, 0.4874808532593264), (36135, 0.4871080384826499), (15112,

...


[(37785, 0.4892997388129983), (46145, 0.48900460786115746), (24324, 0.48836095330555884), (16658, 0.4876801363728499), (33910, 0.4853925953530118), (26818, 0.484012456839613), (39468, 0.4804123865607956), (16616, 0.47893718898816684), (23165, 0.47793018362327006), (24000, 0.4779279854278091), (6264, 0.477048172755752), (1159, 0.47693446311682824), (11487, 0.47654448004033156), (38256, 0.4746873984531269), (16464, 0.47462418355229424), (23038, 0.47408289097414463), (32379, 0.47392078127453435), (8245, 0.4733119015361589), (25074, 0.47292441456389606), (10494, 0.4727512655201302), (11928, 0.4721484845567757), (46019, 0.4718343160053964), (22702, 0.47116712070877803), (46027, 0.4689891237639), (38948, 0.46879958815341916), (30080, 0.46853840286643217), (28446, 0.4683787096938639), (38213, 0.4681038534778884), (22960, 0.4680783541025709), (26183, 0.4678802949126382), (10612, 0.46621604830276103), (20286, 0.4659704155577032), (10602, 0.4657811090287976), (5600, 0.46572938134163255), (28733

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




[(12354, 0.4338584540347389), (10053, 0.4314578550314448), (39181, 0.4311445702869493), (43115, 0.4310629483086321), (5933, 0.4308753956706446), (6570, 0.43020305916199914), (31446, 0.4301996276652766), (19964, 0.4300183622008177), (6629, 0.42968458860846576), (18132, 0.4296537579766411), (6423, 0.4291746006772729), (13273, 0.42901030273368623), (6908, 0.4289626663095247), (45308, 0.4288208699096054), (6394, 0.42711610008817075), (22630, 0.4269109048508288), (2487, 0.42658526223029164), (19620, 0.4265145934352373), (16857, 0.42585450988671447), (10572, 0.4253971795394101), (16076, 0.4247630871347779), (6623, 0.4242614312078858), (27538, 0.4241260592759597), (17386, 0.42402077007823935), (10239, 0.42392446085807145), (9296, 0.423916966857714), (26588, 0.4233276819052632), (44884, 0.422992089816021), (14036, 0.4225980317061138), (19040, 0.4216431336566093), (37123, 0.4216134115434651), (42165, 0.4213949126468572), (10613, 0.42138224977537525), (35600, 0.4209781586659802), (32468, 0.4209

[(466, 0.5216573288382819), (12219, 0.5097009433939459), (22271, 0.5021460012594338), (34204, 0.4976332643532133), (38522, 0.49153749334439667), (18783, 0.48499649801638767), (40275, 0.4849941420083168), (40890, 0.48433419137479805), (45043, 0.48281753654299103), (17619, 0.47945728896580914), (27774, 0.4789545442596739), (15125, 0.4788930953247709), (8231, 0.47853329173171033), (39116, 0.47764342912196006), (11073, 0.476516403511204), (18278, 0.47650398979306446), (31333, 0.4754073025718694), (28875, 0.47467386179004045), (22086, 0.4738381763797724), (22230, 0.4736019469117517), (37484, 0.47331411101186943), (24543, 0.4713652578650988), (21678, 0.4711165561319815), (18864, 0.47110781277132674), (40031, 0.4710166439200691), (43141, 0.47069393897556566), (13244, 0.47034657757788284), (22494, 0.47022499469230195), (26735, 0.47001899166280514), (34389, 0.46942097393064997), (43260, 0.4688036755834512), (15662, 0.4683840826310272), (43056, 0.46783939752674186), (13910, 0.46706129984471817),

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [140]:
#Biology dataset - Question body and title
pickle.dump(ques_recommendations,open("ques_recommendations.dat","wb"))
pickle.dump(ans_recommendations,open("ans_recommendations.dat","wb"))
pickle.dump(combinedRecommendations,open("que_ans_recommendations.dat","wb"))

In [158]:
#Biology dataset - only title
pickle.dump(ques_recommendations,open("title_ques_recommendations.dat","wb"))
pickle.dump(combinedRecommendations,open("title_que_ans_recommendations.dat","wb"))

In [177]:
#Biology dataset - tag+title+body
pickle.dump(ques_recommendations,open("w_tags_ques_recommendations.dat","wb"))
pickle.dump(combinedRecommendations,open("w_tags_que_ans_recommendations.dat","wb"))

In [94]:
#Biology dataset: Question, body+title+tag hybrid recommendations
pickle.dump(ques_recommendations,open("bio_ques_hybrid_recommendations.dat","wb"))

In [101]:
#Biology dataset: Answer recommendations--hybrid
pickle.dump(ans_recommendations,open("bio_ans_hybrid_recommendations.dat","wb"))

In [105]:
#Biology dataset: Combined recommendations - Hybrid
pickle.dump(combinedRecommendations,open("bio_combined_hybrid_recommendations.dat","wb"))

In [126]:
#Datascience dataset: Question hybrid recommendations
pickle.dump(ques_recommendations,open("ds_ques_hybrid_recommendations.dat","wb"))

In [29]:
#datascience: Answer hybrid recommendations
pickle.dump(ans_recommendations,open("ds_ans_hybrid_recommendations.dat","wb"))

In [2]:
import pickle
ds_combined_recommendations = pickle.load(open("ds_combined_recommendations.dat","rb"))

In [135]:
import pickle
#Datascience dataset: Questions, hybrid recommendations: Normalized
pickle.dump(ques_recommendations,open("n_ds_ques_hybrid_recommendations.dat","wb"))

In [77]:
#data-science answer recommendations
pickle.dump(ans_recommendations,open("n_ds_ans_hybrid_recommendations.dat","wb"))

In [79]:
#datascience, combined recommendations, Normalized, hybrid
pickle.dump(combinedRecommendations,open("n_ds_combined_hybrid_recommendations.dat","wb"))

In [114]:
#Biology: Question recommendations: Normalized: Hybrid
pickle.dump(ques_recommendations,open("n_bio_ques_hybrid_recommendations.dat","wb"))

In [61]:
#Biology: Answer recommendations: Normalized: Hybrid
pickle.dump(ans_recommendations,open("n_bio_ans_hybrid_recommendations.dat","wb"))

In [117]:
#Biology: combined recommendations: Normalized, hybrid
pickle.dump(combinedRecommendations,open("n_bio_combined_hybrid_recommendations.dat","wb"))